# Installing Dependencies

In [1]:
!pip install transformers datasets torch accelerate huggingface_hub

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 542.0/542.0 kB 9.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.4/302.4 kB 33.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 12.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 11.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 401.2/401.2 kB 36.2 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64

In [2]:
from huggingface_hub import notebook_login
notebook_login()

# Import Libraries

In [3]:
import torch
from transformers import GPT2LMHeadModel, GPT2Tokenizer
from transformers import TrainingArguments, Trainer
from datasets import load_dataset, load_metric

# Import Model

In [34]:
model_name = "gpt2"
model = GPT2LMHeadModel.from_pretrained(model_name)
tokenizer = GPT2Tokenizer.from_pretrained(model_name)
tokenizer.save_pretrained("./gpt2-evy")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


('./gpt2-evy/tokenizer_config.json',
 './gpt2-evy/special_tokens_map.json',
 './gpt2-evy/vocab.json',
 './gpt2-evy/merges.txt',
 './gpt2-evy/added_tokens.json')

In [35]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

tokenizer.pad_token = tokenizer.eos_token

dataset = load_dataset("joshcarp/evy-dataset")

train_data = dataset["train"].select([i for i in range(len(dataset["train"])) if i % 10 != 0])  # Use 90% of the data for training
val_data = dataset["train"].select([i for i in range(len(dataset["train"])) if i % 10 == 0])  # Use 10% of the data for validation

def tokenize_function(examples):
    inputs = tokenizer(examples['contents'], return_tensors='pt', padding='max_length', max_length=512, truncation=True)
    return {'input_ids': inputs['input_ids'], 'labels': inputs['input_ids']}

train_data = train_data.map(tokenize_function, batched=True)
val_data = val_data.map(tokenize_function, batched=True)

In [17]:
device

device(type='cuda')

# Train Model

In [36]:
# Define training arguments
training_args = TrainingArguments(
    output_dir='./gpt2-evy',
    overwrite_output_dir=True,
    num_train_epochs=20,
    per_device_train_batch_size=8,
    evaluation_strategy="epoch",
    eval_steps=1000,
    save_steps=1000,
    logging_steps=100,
    logging_dir='./logs',
    push_to_hub=True,
    # resume_from_checkpoint="./gpt2-evy/checkpoint-1900"
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_data,
    eval_dataset=val_data,
    tokenizer=tokenizer
)

trainer.train()

TrainOutput(global_step=140, training_loss=0.9502299581255231, metrics={'train_runtime': 38.6687, 'train_samples_per_second': 27.93, 'train_steps_per_second': 3.621, 'total_flos': 282195394560000.0, 'train_loss': 0.9502299581255231, 'epoch': 20.0})

# Save Model

In [37]:
trainer.save_model()
trainer.push_to_hub()
tokenizer.push_to_hub("gpt2-evy")

model.safetensors:   0%|          | 0.00/498M [00:00<?, ?B/s]

README.md:   0%|          | 0.00/2.19k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/joshcarp/gpt2-evy/commit/c95869e260cd381e108a4f2ad1c6f3745a001a68', commit_message='Upload tokenizer', commit_description='', oid='c95869e260cd381e108a4f2ad1c6f3745a001a68', pr_url=None, pr_revision=None, pr_num=None)